# TP2 - Modeling using docplex

## 1. The `docplex` python package

`DOcplex` is a python package developped by IBM &mdash; It provides easy-to-use API for IBM solvers Cplex and Cpoptimizer.

DOcplex documentation for mathematical programming can be found here: http://ibmdecisionoptimization.github.io/docplex-doc/#mathematical-programming-modeling-for-python-using-docplex-mp-docplex-mp

## 2. Solving TSP using `docplex`

### 2.1. TSP model using `docplex`

**Exercice:** Using `docplex`, create a model for the travelling salesman problem using the MTZ or Flow formulation and compare them.

In [ ]:
from docplex.mp.model import Model
import tsp.data as data

distances = data.grid42
N = len(distances)

tsp = Model("TSP")
tsp.log_output = True

...  # TODO

solution = tsp.solve()
print("z* =", solution.objective_value)

The largest set of distances contains 42 nodes, and should be easily solved by `docplex`.

### 2.2. Generating random TSP instances

**Question:** What method could you implement to generate a realistic set of distances for $n$ customers?

**Exercice:** Implement the method proposed above and test it.

In [ ]:
import numpy as np
import scipy.spatial.distance


def generate_distances(n: int):
    ...  # TODO


from docplex.mp.model import Model

distances = generate_distances(50)
print(distances)

N = len(distances)

tsp = Model("TSP")
tsp.log_output = True

...  # TODO: Copy your model from the first question here.

solution = tsp.solve()
print("z* =", solution.objective_value)

## 3. Solving Warehouse Allocation using Benders decomposition with `docplex`

### 3.1. The warehouse problem

A company needs to supply a set of $n$ clients and needs to open new warehouses (from a
set of $m$ possible warehouses).
Opening a warehouse $j$ costs $f_j$ and supplying a client $i$ from a warehouse $j$ costs $c_{ij}$ per supply unit.
Which warehouses should be opened in order to satisfy all clients while minimizing the total cost?

### 3.2. Solving the warehouse problem with a single ILP

- $y_{j} = 1$ if and only if warehouse $j$ is opened.
- $x_{ij}$ is the fraction supplied from warehouse $j$ to customer $i$.

$
\begin{align}
  \text{min.} \quad & \sum_{i=1}^{n} \sum_{j=1}^{m} c_{ij} x_{ij} + \sum_{j=1}^{m} f_{j} y_{j} & \\
  \text{s.t.} \quad & \sum_{j=1}^{m} x_{ij} = 1, & \forall i \in\{1,\ldots,n\}\\
                    & x_{ij} \leq y_{j}, & \forall i\in\{1,\ldots,n\},\forall j\in\{1,\ldots,m\}\\
                    & y_{j} \in \left\{0,~1\right\}, & \forall j \in \left\{1,~\ldots,~m\right\}\\
                    & x_{ij} \geq 0, & \forall i \in \left\{1,~\ldots,~n\right\}, \forall j \in \left\{1,~\ldots,~m\right\}
\end{align}
$


**Exercice:** Implement the ILP model for the warehouse allocation problem and test it on the given instance.

In [1]:
from docplex.mp.model import Model
#import numpy as np

# We will start with a small instances with 3 warehouses and 3 clients:
M = 3
N = 3


# Opening and distribution costs:
f = [20, 20, 20]
c = [[15, 1, 2], [1, 16, 3], [4, 1, 17]]

wa = Model("Warehouse Allocation")
wa.log_output = True

x = [wa.continuous_var_list(M, name=f"x{i}") for i in range(N)]
y = wa.binary_var_list(M)

#wa.set_objective("min", np.multiply(x, c) + np.multiply(y, f))
wa.set_objective("min",  sum(c[i][j]*x[i][j] for i in range(N) for j in range(M)) + sum(f[j]*y[j] for j in range(M)))


for i in range(N):
    wa.add_constraint(sum(x[i][j] for j in range(M)) == 1)
    for j in range(M):
        wa.add_constraint(x[i][j] <= y[j])
        wa.add_constraint(x[i][j] >= 0)

solution = wa.solve()
print("z* =", solution.objective_value)

CPXPARAM_Read_DataCheck                          1
Found incumbent of value 40.000000 after 0.01 sec. (0.00 ticks)
Tried aggregator 1 time.
MIP Presolve eliminated 9 rows and 0 columns.
Reduced MIP has 12 rows, 12 columns, and 27 nonzeros.
Reduced MIP has 3 binaries, 0 generals, 0 SOSs, and 0 indicators.
Presolve time = 0.01 sec. (0.02 ticks)
Probing time = 0.00 sec. (0.00 ticks)
Tried aggregator 1 time.
Reduced MIP has 12 rows, 12 columns, and 27 nonzeros.
Reduced MIP has 3 binaries, 0 generals, 0 SOSs, and 0 indicators.
Presolve time = 0.00 sec. (0.02 ticks)
Probing time = 0.00 sec. (0.00 ticks)
MIP emphasis: balance optimality and feasibility.
MIP search method: dynamic search.
Parallel mode: deterministic, using up to 32 threads.
Root relaxation solution time = 0.00 sec. (0.02 ticks)

        Nodes                                         Cuts/
   Node  Left     Objective  IInf  Best Integer    Best Bound    ItCnt     Gap

*     0+    0                           40.0000        0.000

### 3.3. Benders' decomposition for the Warehouse Allocation problem

We are going to use Benders' decomposition to solve the Warehouse Allocation problem. 

#### Dual subproblem

$
\begin{align*}
\text{max.} \quad & \sum_{i=1}^{n} v_{i} - \sum_{i=1}^{n}\sum_{j=1}^{m} \bar{y}_{j} u_{ij} & \\
\text{s.t.} \quad & v_{i} - u_{ij} \leq c_{ij}, & \forall i\in\{1,\ldots,n\},\forall j\in\{1,\ldots,m\}\\
                  & v_{i} \in\mathbb{R},\ u_{ij} \geq 0 & \forall i \in\{1,\ldots,n\}, \forall j\in\{1,\ldots,m\}
\end{align*}
$

#### Master problem

$
\begin{align*}
  \text{min.} \quad & \sum_{j=1}^{m} f_j y_j + z & \\
  \text{s.t.} \quad & z \geq \sum_{i=1}^{n}v_i^p - \sum_{i=1}^{n} \sum_{j=1}^{m} u_{ij}^p y_j, & \forall p\in l_1\\
                    & 0 \geq \sum_{i=1}^{n}v_i^r - \sum_{i=1}^{n} \sum_{j=1}^{n} u_{ij}^r y_j, & \forall r\in l_2\\
                    & y_{j} \in\{0,1\}, & \forall j\in\{1,\ldots,m\}
\end{align*}
$

**Exercice:** Implement the method `create_master_problem` that creates the initial master problem (without feasibility or optimality constraints) for the warehouse allocation problem.

<div class="alert alert-info alert-block">

You can use `print(m.export_as_lp_string())` to display a textual representation of a `docplex` model `m`.
    
</div>

In [2]:
from docplex.mp.model import Model
from docplex.mp.linear import Var
from docplex.mp.constr import AbstractConstraint
from typing import List, Sequence, Tuple


def create_master_problem(
    N: int, M: int, f: Sequence[float], c: Sequence[Sequence[float]]
) -> Tuple[Model, Var, Sequence[Var]]:
    """
    Creates the initial Benders master problem for the Warehouse Allocation problem.

    Args:
        N: Number of clients.
        M: Number of warehouses.
        f: Array-like containing costs of opening warehouses.
        c: 2D-array like containing transport costs from client to warehouses.

    Returns:
        A 3-tuple containing the docplex problem, the z variable and the y variables.
    """

    wa = Model("Warehouse Allocation - Benders master problem")

    z = wa.continuous_var()
    y = wa.binary_var_list(M)
    
    
    wa.set_objective("min", sum(f[j]*y[j] for j in range(M)) + z)

    return wa, z, y


# Check your method:
wa, z, y = create_master_problem(N, M, f, c)
print(wa.export_as_lp_string())

\ This file has been generated by DOcplex
\ ENCODING=ISO-8859-1
\Problem name: Warehouse Allocation - Benders master problem

Minimize
 obj: x1 + 20 x2 + 20 x3 + 20 x4
Subject To

Bounds
 0 <= x2 <= 1
 0 <= x3 <= 1
 0 <= x4 <= 1

Binaries
 x2 x3 x4
End



**Exercice:** Implement the method `add_optimality_constraints` that add optimality constraints to the Benders master problem. 

In [3]:
def add_optimality_constraint(
    N: int,
    M: int,
    wa: Model,
    z: Var,
    y: Sequence[Var],
    v: Sequence[float],
    u: Sequence[Sequence[float]],
) -> List[AbstractConstraint]:
    """
    Adds an optimality constraints to the given Warehouse Allocation model
    using the given optimal values from the Benders dual subproblem.

    Args:
        N: Number of clients.
        M: Number of warehouses.
        wa: The Benders master problem (docplex.mp.model.Model).
        z: The z variable of the master problem.
        y: The y variables of the master problem.
        v: The optimal values for the v variables of the Benders dual subproblem.
        u: The optimal values for the u variables of the Benders dual subproblem.

    Return: The optimality constraint added.
    """
    constraint = wa.add_constraint(z >= (sum(v[i] for i in range(N)) - sum(u[i][j]*y[j] for i in range(N) for j in range(M))))
    return constraint

**Exercice:** Implement the method `add_feasibility_constraints` that add feasibility constraints to the Benders master problem. 

In [4]:
def add_feasibility_constraints(
    N: int,
    M: int,
    wa: Model,
    z: Var,
    y: Sequence[Var],
    v: Sequence[float],
    u: Sequence[Sequence[float]],
) -> List[AbstractConstraint]:
    """
    Adds an optimality constraints to the given Warehouse Allocation model
    using the given optimal values from the Benders dual subproblem.

    Args:
      - N: Number of clients.
      - M: Number of warehouses.
      - wa: The Benders master problem (docplex.mp.model.Model).
      - z: The z variable of the master problem.
      - y: The y variables of the master problem.
      - v: The extreme rays for the v variables of the Benders dual subproblem.
      - u: The extreme rays for the u variables of the Benders dual subproblem.

    Returns:
        The feasibility constraint added.
    """
    constraint =  wa.add_constraint(0 >= sum(v[i] for i in range(N)) - sum(u[i][j]*y[j] for i in range(N) for j in range(M)))
    return constraint

**Exercice:** Implement the method `create_dual_subproblem` that, given a solution `y` of the master problem, create the corresponding Benders dual subproblem.

$
\begin{align*}
\text{max.} \quad & \sum_{i=1}^{n} v_{i} - \sum_{i=1}^{n}\sum_{j=1}^{m} \bar{y}_{j} u_{ij} & \\
\text{s.t.} \quad & v_{i} - u_{ij} \leq c_{ij}, & \forall i\in\{1,\ldots,n\},\forall j\in\{1,\ldots,m\}\\
                  & v_{i} \in\mathbb{R},\ u_{ij} \geq 0 & \forall i \in\{1,\ldots,n\}, \forall j\in\{1,\ldots,m\}
\end{align*}
$

In [5]:
from docplex.mp.model import Model
import math


def create_dual_subproblem(
    N: int, M: int, f: Sequence[float], c: Sequence[Sequence[float]], y: Sequence[int]
) -> Tuple[Model, Sequence[Var], Sequence[Sequence[Var]]]:
    """
    Creates a Benders dual subproblem for the Warehouse Allocation problem corresponding
    to the given master solution.

    Args:
        N: Number of clients.
        M: Number of warehouses.
        f: Array-like containing costs of opening warehouses.
        c: 2D-array like containing transport costs from client to warehouses.
        y: Values of the y variables from the Benders master problem.

    Returns:
        A 3-tuple containing the docplex problem, the v variable and the u variables.
    """

    dsp = Model("Warehouse Allocation - Benders dual subproblem")

    # We disable pre-solve to be able to retrieve a meaningful status in the main
    # algorithm:
    dsp.parameters.preprocessing.presolve.set(0)
    v = dsp.continuous_var_list(M, lb=-math.inf, name=f"v")
    u = [dsp.continuous_var_list(M, name=f"u{i}") for i in range(M)]
    
    dsp.set_objective("max", sum(v[i] for i in range(N)) - sum(y[j]*u[i][j] for i in range(N) for j in range(M)))
    
    for i in range(N):
        for j in range(M):
            dsp.add_constraint(v[i] - u[i][j] <= c[i][j])
            dsp.add_constraint(u[i][j] >= 0)

    return dsp, v, u


# Check your method (assuming y = [1 1 1 ... 1]):
dsp, v, u = create_dual_subproblem(N, M, f, c, [1] * M)
print(dsp.export_as_lp_string())

\ This file has been generated by DOcplex
\ ENCODING=ISO-8859-1
\Problem name: Warehouse Allocation - Benders dual subproblem

Maximize
 obj: v_0 + v_1 + v_2 - u0_0 - u0_1 - u0_2 - u1_0 - u1_1 - u1_2 - u2_0 - u2_1
      - u2_2
Subject To
 c1: v_0 - u0_0 <= 15
 c2: u0_0 >= 0
 c3: v_0 - u0_1 <= 1
 c4: u0_1 >= 0
 c5: v_0 - u0_2 <= 2
 c6: u0_2 >= 0
 c7: v_1 - u1_0 <= 1
 c8: u1_0 >= 0
 c9: v_1 - u1_1 <= 16
 c10: u1_1 >= 0
 c11: v_1 - u1_2 <= 3
 c12: u1_2 >= 0
 c13: v_2 - u2_0 <= 4
 c14: u2_0 >= 0
 c15: v_2 - u2_1 <= 1
 c16: u2_1 >= 0
 c17: v_2 - u2_2 <= 17
 c18: u2_2 >= 0

Bounds
       v_0 Free
       v_1 Free
       v_2 Free
End



**Exercice:** Using the methods you implemented, write the Benders decomposition algorithm for the warehouse allocation problem.

<div class="alert alert-block alert-info">

The `get_extreme_rays` function can be used to retrieve the extreme rays associated with an unbounded solution of the dual subproblem.
    
</div>

<div class="alert alert-block alert-info">
    
You can use `model.get_solve_status()` to obtain the status of the resolution and compare it to members of `JobSolveStatus`:
    
```python
if model.get_solve_status() == JobSolveStatus.OPTIMAL_SOLUTION:
    pass
```
    
</div>

In [ ]:
from docplex.mp.model import Model
from docplex.util.status import JobSolveStatus


def get_extreme_rays(
    N: int, M: int, model: Model, v: Sequence[Var], u: Sequence[Sequence[Var]]
) -> Tuple[Sequence[float], Sequence[Sequence[float]]]:
    """
    Retrieves the extreme rays associated to the dual subproblem.

    Args:
        N: Number of clients.
        M: Number of warehouses.
        model: The Benders dual subproblem model (docplex.mp.model.Model).
        v: 1D array containing the v variables of the subproblem.
        u: Either a 2D array of a tuple-index dictionary containing the u variables
            of the subproblem.

    Returns:
        A 2-tuple containing the list of extreme rays correspondig to v,
        and the 2D-list of extreme rays corresponding to u.
    """
    ray = model.get_engine().get_cplex().solution.advanced.get_ray()

    if isinstance(u, dict):

        def get_uij(i, j):
            return u[i, j]

    else:

        def get_uij(i, j):
            return u[i][j]

    return (
        [ray[v[i].index] for i in range(N)],
        [[ray[get_uij(i, j).index] for j in range(M)] for i in range(N)],
    )


# We will start with a small instances with 3 warehouses and 3 clients:
N = 3
M = 3

# Opening and distribution costs:
f = [20, 20, 20]
c = [[15, 1, 2], [1, 16, 3], [4, 1, 17]]

# We stop iterating if the new solution is less than epsilon
# better than the previous one:
epsilon = 1e-6

wa, z, y = create_master_problem(N, M, f, c)

n = 0
while True:

    # Print iteration:
    n = n + 1
    print("Iteration {}".format(n))

    ...  # TODO

print("Done.")

Iteration 1
Iteration 2
Iteration 3
Iteration 4
Iteration 5
Iteration 6
Iteration 7
Iteration 8
Iteration 9
Iteration 10
Iteration 11
Iteration 12
Iteration 13
Iteration 14
Iteration 15
Iteration 16
Iteration 17
Iteration 18
Iteration 19
Iteration 20
Iteration 21
Iteration 22
Iteration 23
Iteration 24
Iteration 25
Iteration 26
Iteration 27
Iteration 28
Iteration 29
Iteration 30
Iteration 31
Iteration 32
Iteration 33
Iteration 34
Iteration 35
Iteration 36
Iteration 37
Iteration 38
Iteration 39
Iteration 40
Iteration 41
Iteration 42
Iteration 43
Iteration 44
Iteration 45
Iteration 46
Iteration 47
Iteration 48
Iteration 49
Iteration 50
Iteration 51
Iteration 52
Iteration 53
Iteration 54
Iteration 55
Iteration 56
Iteration 57
Iteration 58
Iteration 59
Iteration 60
Iteration 61
Iteration 62
Iteration 63
Iteration 64
Iteration 65
Iteration 66
Iteration 67
Iteration 68
Iteration 69
Iteration 70
Iteration 71
Iteration 72
Iteration 73
Iteration 74
Iteration 75
Iteration 76
Iteration 77
Iteratio

Iteration 2158
Iteration 2159
Iteration 2160
Iteration 2161
Iteration 2162
Iteration 2163
Iteration 2164
Iteration 2165
Iteration 2166
Iteration 2167
Iteration 2168
Iteration 2169
Iteration 2170
Iteration 2171
Iteration 2172
Iteration 2173
Iteration 2174
Iteration 2175
Iteration 2176
Iteration 2177
Iteration 2178
Iteration 2179
Iteration 2180
Iteration 2181
Iteration 2182
Iteration 2183
Iteration 2184
Iteration 2185
Iteration 2186
Iteration 2187
Iteration 2188
Iteration 2189
Iteration 2190
Iteration 2191
Iteration 2192
Iteration 2193
Iteration 2194
Iteration 2195
Iteration 2196
Iteration 2197
Iteration 2198
Iteration 2199
Iteration 2200
Iteration 2201
Iteration 2202
Iteration 2203
Iteration 2204
Iteration 2205
Iteration 2206
Iteration 2207
Iteration 2208
Iteration 2209
Iteration 2210
Iteration 2211
Iteration 2212
Iteration 2213
Iteration 2214
Iteration 2215
Iteration 2216
Iteration 2217
Iteration 2218
Iteration 2219
Iteration 2220
Iteration 2221
Iteration 2222
Iteration 2223
Iteration 

Iteration 3950
Iteration 3951
Iteration 3952
Iteration 3953
Iteration 3954
Iteration 3955
Iteration 3956
Iteration 3957
Iteration 3958
Iteration 3959
Iteration 3960
Iteration 3961
Iteration 3962
Iteration 3963
Iteration 3964
Iteration 3965
Iteration 3966
Iteration 3967
Iteration 3968
Iteration 3969
Iteration 3970
Iteration 3971
Iteration 3972
Iteration 3973
Iteration 3974
Iteration 3975
Iteration 3976
Iteration 3977
Iteration 3978
Iteration 3979
Iteration 3980
Iteration 3981
Iteration 3982
Iteration 3983
Iteration 3984
Iteration 3985
Iteration 3986
Iteration 3987
Iteration 3988
Iteration 3989
Iteration 3990
Iteration 3991
Iteration 3992
Iteration 3993
Iteration 3994
Iteration 3995
Iteration 3996
Iteration 3997
Iteration 3998
Iteration 3999
Iteration 4000
Iteration 4001
Iteration 4002
Iteration 4003
Iteration 4004
Iteration 4005
Iteration 4006
Iteration 4007
Iteration 4008
Iteration 4009
Iteration 4010
Iteration 4011
Iteration 4012
Iteration 4013
Iteration 4014
Iteration 4015
Iteration 

Iteration 6234
Iteration 6235
Iteration 6236
Iteration 6237
Iteration 6238
Iteration 6239
Iteration 6240
Iteration 6241
Iteration 6242
Iteration 6243
Iteration 6244
Iteration 6245
Iteration 6246
Iteration 6247
Iteration 6248
Iteration 6249
Iteration 6250
Iteration 6251
Iteration 6252
Iteration 6253
Iteration 6254
Iteration 6255
Iteration 6256
Iteration 6257
Iteration 6258
Iteration 6259
Iteration 6260
Iteration 6261
Iteration 6262
Iteration 6263
Iteration 6264
Iteration 6265
Iteration 6266
Iteration 6267
Iteration 6268
Iteration 6269
Iteration 6270
Iteration 6271
Iteration 6272
Iteration 6273
Iteration 6274
Iteration 6275
Iteration 6276
Iteration 6277
Iteration 6278
Iteration 6279
Iteration 6280
Iteration 6281
Iteration 6282
Iteration 6283
Iteration 6284
Iteration 6285
Iteration 6286
Iteration 6287
Iteration 6288
Iteration 6289
Iteration 6290
Iteration 6291
Iteration 6292
Iteration 6293
Iteration 6294
Iteration 6295
Iteration 6296
Iteration 6297
Iteration 6298
Iteration 6299
Iteration 

Iteration 8354
Iteration 8355
Iteration 8356
Iteration 8357
Iteration 8358
Iteration 8359
Iteration 8360
Iteration 8361
Iteration 8362
Iteration 8363
Iteration 8364
Iteration 8365
Iteration 8366
Iteration 8367
Iteration 8368
Iteration 8369
Iteration 8370
Iteration 8371
Iteration 8372
Iteration 8373
Iteration 8374
Iteration 8375
Iteration 8376
Iteration 8377
Iteration 8378
Iteration 8379
Iteration 8380
Iteration 8381
Iteration 8382
Iteration 8383
Iteration 8384
Iteration 8385
Iteration 8386
Iteration 8387
Iteration 8388
Iteration 8389
Iteration 8390
Iteration 8391
Iteration 8392
Iteration 8393
Iteration 8394
Iteration 8395
Iteration 8396
Iteration 8397
Iteration 8398
Iteration 8399
Iteration 8400
Iteration 8401
Iteration 8402
Iteration 8403
Iteration 8404
Iteration 8405
Iteration 8406
Iteration 8407
Iteration 8408
Iteration 8409
Iteration 8410
Iteration 8411
Iteration 8412
Iteration 8413
Iteration 8414
Iteration 8415
Iteration 8416
Iteration 8417
Iteration 8418
Iteration 8419
Iteration 

...

Iteration 349272
Iteration 349273
Iteration 349274
Iteration 349275
Iteration 349276
Iteration 349277
Iteration 349278
Iteration 349279
Iteration 349280
Iteration 349281
Iteration 349282
Iteration 349283
Iteration 349284
Iteration 349285
Iteration 349286
Iteration 349287
Iteration 349288
Iteration 349289
Iteration 349290
Iteration 349291
Iteration 349292
Iteration 349293
Iteration 349294
Iteration 349295
Iteration 349296
Iteration 349297
Iteration 349298
Iteration 349299
Iteration 349300
Iteration 349301
Iteration 349302
Iteration 349303
Iteration 349304
Iteration 349305
Iteration 349306
Iteration 349307
Iteration 349308
Iteration 349309
Iteration 349310
Iteration 349311
Iteration 349312
Iteration 349313
Iteration 349314
Iteration 349315
Iteration 349316
Iteration 349317
Iteration 349318
Iteration 349319
Iteration 349320
Iteration 349321
Iteration 349322
Iteration 349323
Iteration 349324
Iteration 349325
Iteration 349326
Iteration 349327
Iteration 349328
Iteration 349329
Iteration 3493

Iteration 351656
Iteration 351657
Iteration 351658
Iteration 351659
Iteration 351660
Iteration 351661
Iteration 351662
Iteration 351663
Iteration 351664
Iteration 351665
Iteration 351666
Iteration 351667
Iteration 351668
Iteration 351669
Iteration 351670
Iteration 351671
Iteration 351672
Iteration 351673
Iteration 351674
Iteration 351675
Iteration 351676
Iteration 351677
Iteration 351678
Iteration 351679
Iteration 351680
Iteration 351681
Iteration 351682
Iteration 351683
Iteration 351684
Iteration 351685
Iteration 351686
Iteration 351687
Iteration 351688
Iteration 351689
Iteration 351690
Iteration 351691
Iteration 351692
Iteration 351693
Iteration 351694
Iteration 351695
Iteration 351696
Iteration 351697
Iteration 351698
Iteration 351699
Iteration 351700
Iteration 351701
Iteration 351702
Iteration 351703
Iteration 351704
Iteration 351705
Iteration 351706
Iteration 351707
Iteration 351708
Iteration 351709
Iteration 351710
Iteration 351711
Iteration 351712
Iteration 351713
Iteration 3517

Iteration 353554
Iteration 353555
Iteration 353556
Iteration 353557
Iteration 353558
Iteration 353559
Iteration 353560
Iteration 353561
Iteration 353562
Iteration 353563
Iteration 353564
Iteration 353565
Iteration 353566
Iteration 353567
Iteration 353568
Iteration 353569
Iteration 353570
Iteration 353571
Iteration 353572
Iteration 353573
Iteration 353574
Iteration 353575
Iteration 353576
Iteration 353577
Iteration 353578
Iteration 353579
Iteration 353580
Iteration 353581
Iteration 353582
Iteration 353583
Iteration 353584
Iteration 353585
Iteration 353586
Iteration 353587
Iteration 353588
Iteration 353589
Iteration 353590
Iteration 353591
Iteration 353592
Iteration 353593
Iteration 353594
Iteration 353595
Iteration 353596
Iteration 353597
Iteration 353598
Iteration 353599
Iteration 353600
Iteration 353601
Iteration 353602
Iteration 353603
Iteration 353604
Iteration 353605
Iteration 353606
Iteration 353607
Iteration 353608
Iteration 353609
Iteration 353610
Iteration 353611
Iteration 3536

Iteration 355270
Iteration 355271
Iteration 355272
Iteration 355273
Iteration 355274
Iteration 355275
Iteration 355276
Iteration 355277
Iteration 355278
Iteration 355279
Iteration 355280
Iteration 355281
Iteration 355282
Iteration 355283
Iteration 355284
Iteration 355285
Iteration 355286
Iteration 355287
Iteration 355288
Iteration 355289
Iteration 355290
Iteration 355291
Iteration 355292
Iteration 355293
Iteration 355294
Iteration 355295
Iteration 355296
Iteration 355297
Iteration 355298
Iteration 355299
Iteration 355300
Iteration 355301
Iteration 355302
Iteration 355303
Iteration 355304
Iteration 355305
Iteration 355306
Iteration 355307
Iteration 355308
Iteration 355309
Iteration 355310
Iteration 355311
Iteration 355312
Iteration 355313
Iteration 355314
Iteration 355315
Iteration 355316
Iteration 355317
Iteration 355318
Iteration 355319
Iteration 355320
Iteration 355321
Iteration 355322
Iteration 355323
Iteration 355324
Iteration 355325
Iteration 355326
Iteration 355327
Iteration 3553

Iteration 357270
Iteration 357271
Iteration 357272
Iteration 357273
Iteration 357274
Iteration 357275
Iteration 357276
Iteration 357277
Iteration 357278
Iteration 357279
Iteration 357280
Iteration 357281
Iteration 357282
Iteration 357283
Iteration 357284
Iteration 357285
Iteration 357286
Iteration 357287
Iteration 357288
Iteration 357289
Iteration 357290
Iteration 357291
Iteration 357292
Iteration 357293
Iteration 357294
Iteration 357295
Iteration 357296
Iteration 357297
Iteration 357298
Iteration 357299
Iteration 357300
Iteration 357301
Iteration 357302
Iteration 357303
Iteration 357304
Iteration 357305
Iteration 357306
Iteration 357307
Iteration 357308
Iteration 357309
Iteration 357310
Iteration 357311
Iteration 357312
Iteration 357313
Iteration 357314
Iteration 357315
Iteration 357316
Iteration 357317
Iteration 357318
Iteration 357319
Iteration 357320
Iteration 357321
Iteration 357322
Iteration 357323
Iteration 357324
Iteration 357325
Iteration 357326
Iteration 357327
Iteration 3573

### 3.4. Generating instances for the Warehouse Allocation problem

**Exercice:** Using the TSP instances contained in `tsp.data` or the `generate_distances` method, create instances for the warehouse allocation problem with randomized opening costs.

<div class="alert alert-block alert-danger"></div>